In [2]:
import pandas as pd
import csv

In [9]:
# Specify the path to your CSV file
file_path = 'styles.csv'

headers = []
data = []

# Open the CSV file
with open(file_path, mode='r', newline='') as file:
    # Create a CSV reader object
    csv_reader = csv.reader(file)
    
    # Iterate over each row in the CSV file
    for row in csv_reader:
        # Print each row (you can replace this with any other operation you want to perform on the row)
        headers = row
        break
    for row in csv_reader:
        if len(row) != 10:
            pass
        else:
            data.append(row)

In [10]:
styles_df = pd.DataFrame(data,columns=headers)
styles_df

id gender masterCategory subCategory            articleType  \
0      15970    Men        Apparel     Topwear                 Shirts   
1      39386    Men        Apparel  Bottomwear                  Jeans   
2      59263  Women    Accessories     Watches                Watches   
3      21379    Men        Apparel  Bottomwear            Track Pants   
4      53759    Men        Apparel     Topwear                Tshirts   
...      ...    ...            ...         ...                    ...   
44419  17036    Men       Footwear       Shoes           Casual Shoes   
44420   6461    Men       Footwear  Flip Flops             Flip Flops   
44421  18842    Men        Apparel     Topwear                Tshirts   
44422  46694  Women  Personal Care   Fragrance  Perfume and Body Mist   
44423  51623  Women    Accessories     Watches                Watches   

      baseColour  season  year   usage  \
0      Navy Blue    Fall  2011  Casual   
1           Blue  Summer  2012  Casual   
2         Silver  Winter  2016  Casual   
3          Black    Fall  2011  Casual   
4           Grey  Summer  2012  Casual   
...          ...     ...   ...     ...   
44419      White  Summer  2013  Casual   
44420        Red  Summer  2011  Casual   
44421       Blue    Fall  2011  Casual   
44422       Blue  Spring  2017  Casual   
44423       Pink  Winter  2016  Casual   

                                    productDisplayName  
0                     Turtle Check Men Navy Blue Shirt  
1                   Peter England Men Party Blue Jeans  
2                             Titan Women Silver Watch  
3        Manchester United Men Solid Black Track Pants  
4                                Puma Men Grey T-shirt  
...                                                ...  
44419                        Gas Men Caddy Casual Shoe  
44420               Lotto Men's Soccer Track Flip Flop  
44421             Puma Men Graphic Stellar Blue Tshirt  
44422                   Rasasi Women Blue Lady Perfume  
44423  Fossil Women Pink Dial Chronograph Watch ES3050  

[44424 rows x 10 columns]

In [11]:
images_df = pd.read_csv("images.csv")
images_df

filename                                               link
0      15970.jpg  http://assets.myntassets.com/v1/images/style/p...
1      39386.jpg  http://assets.myntassets.com/v1/images/style/p...
2      59263.jpg  http://assets.myntassets.com/v1/images/style/p...
3      21379.jpg  http://assets.myntassets.com/v1/images/style/p...
4      53759.jpg  http://assets.myntassets.com/v1/images/style/p...
...          ...                                                ...
44441  17036.jpg  http://assets.myntassets.com/v1/images/style/p...
44442   6461.jpg  http://assets.myntassets.com/v1/images/style/p...
44443  18842.jpg  http://assets.myntassets.com/v1/images/style/p...
44444  46694.jpg  http://assets.myntassets.com/v1/images/style/p...
44445  51623.jpg  http://assets.myntassets.com/assets/images/516...

[44446 rows x 2 columns]

In [12]:
styles_df['filename'] = styles_df['id'] + ".jpg"

In [13]:
main_df = pd.DataFrame()
main_df = pd.merge(styles_df,images_df,how="inner",on='filename')

In [15]:
main_df.drop(columns=['filename'],inplace=True)

In [16]:
from langchain.docstore.document import Document

In [17]:
main_df.columns

Index(['id', 'gender', 'masterCategory', 'subCategory', 'articleType',
       'baseColour', 'season', 'year', 'usage', 'productDisplayName', 'link'],
      dtype='object')

In [30]:
def make_text(x):
    return (f"""
        Gender is {x['gender']} and 
        masterCategory is {x['masterCategory']} and 
        subCategory is {x['subCategory']} and 
        articleType is {x['articleType']} and 
        baseColour is {x['baseColour']} and 
        season is {x['season']} and 
        year is {x['year']} and 
        usage is {x['usage']} and 
        productDisplayName is {x['productDisplayName']}
    """ , x['id'])

In [34]:
docs_content = main_df.apply(lambda x: make_text(x),axis=1)

In [35]:
docs = []
for text,id in docs_content:
    docs.append(Document(page_content=text,metadata={'id':id}))

In [38]:
import KEYS
from langchain.vectorstores import Chroma
from langchain_google_genai import GoogleGenerativeAIEmbeddings

In [39]:
gemini_embeddings = GoogleGenerativeAIEmbeddings(model="models/text-embedding-004",google_api_key=KEYS.api_key.GOOGLE_API_KEY)

In [40]:
# Save to disk
vectorstore = Chroma.from_documents(
                     documents=docs,                 # Data
                     embedding=gemini_embeddings,    # Embedding model
                     persist_directory="./chroma_db" # Directory to save data
                     )

In [41]:
import chromadb

In [42]:
client = chromadb.PersistentClient(path="./chroma_db")

In [43]:
collection  = client.list_collections()[0]

In [49]:
data = collection.get(include=['documents','metadatas','embeddings'])

embedding_data = []

for id,embedding,_ in zip(data['metadatas'],data['embeddings'],data['documents']):
    embedding_data.append([id['id'],embedding])

In [51]:
embeds_df = pd.DataFrame(embedding_data,columns=['id','embedding'])

In [65]:
final_df = pd.DataFrame()
final_df = pd.merge(main_df,embeds_df,how="inner",on='id')

In [66]:
n_steps = 10
step_size = final_df.shape[0] // n_steps + 1
max_index = final_df.shape[0]
for i in range(0,n_steps):
    final_df.iloc[i * step_size : min(max_index , (i + 1) * step_size)].reset_index().to_feather(f"data_{i}.feather")

In [68]:
df = pd.DataFrame()
for i in range(0,n_steps):
    df = pd.concat([df,pd.read_feather(f"data_{i}.feather")])

index     id gender masterCategory subCategory            articleType  \
0         0  15970    Men        Apparel     Topwear                 Shirts   
1         1  39386    Men        Apparel  Bottomwear                  Jeans   
2         2  59263  Women    Accessories     Watches                Watches   
3         3  21379    Men        Apparel  Bottomwear            Track Pants   
4         4  53759    Men        Apparel     Topwear                Tshirts   
...     ...    ...    ...            ...         ...                    ...   
4432  44419  17036    Men       Footwear       Shoes           Casual Shoes   
4433  44420   6461    Men       Footwear  Flip Flops             Flip Flops   
4434  44421  18842    Men        Apparel     Topwear                Tshirts   
4435  44422  46694  Women  Personal Care   Fragrance  Perfume and Body Mist   
4436  44423  51623  Women    Accessories     Watches                Watches   

     baseColour  season  year   usage  \
0     Navy Blue    Fall  2011  Casual   
1          Blue  Summer  2012  Casual   
2        Silver  Winter  2016  Casual   
3         Black    Fall  2011  Casual   
4          Grey  Summer  2012  Casual   
...         ...     ...   ...     ...   
4432      White  Summer  2013  Casual   
4433        Red  Summer  2011  Casual   
4434       Blue    Fall  2011  Casual   
4435       Blue  Spring  2017  Casual   
4436       Pink  Winter  2016  Casual   

                                   productDisplayName  \
0                    Turtle Check Men Navy Blue Shirt   
1                  Peter England Men Party Blue Jeans   
2                            Titan Women Silver Watch   
3       Manchester United Men Solid Black Track Pants   
4                               Puma Men Grey T-shirt   
...                                               ...   
4432                        Gas Men Caddy Casual Shoe   
4433               Lotto Men's Soccer Track Flip Flop   
4434             Puma Men Graphic Stellar Blue Tshirt   
4435                   Rasasi Women Blue Lady Perfume   
4436  Fossil Women Pink Dial Chronograph Watch ES3050   

                                                   link  \
0     http://assets.myntassets.com/v1/images/style/p...   
1     http://assets.myntassets.com/v1/images/style/p...   
2     http://assets.myntassets.com/v1/images/style/p...   
3     http://assets.myntassets.com/v1/images/style/p...   
4     http://assets.myntassets.com/v1/images/style/p...   
...                                                 ...   
4432  http://assets.myntassets.com/v1/images/style/p...   
4433  http://assets.myntassets.com/v1/images/style/p...   
4434  http://assets.myntassets.com/v1/images/style/p...   
4435  http://assets.myntassets.com/v1/images/style/p...   
4436  http://assets.myntassets.com/assets/images/516...   

                                              embedding  
0     [-0.04959992691874504, 0.030256308615207672, 0...  
1     [-0.04374004527926445, 0.0014770406996831298, ...  
2     [-0.017907867208123207, -0.008326959796249866,...  
3     [-0.06801198422908783, 0.011990022845566273, 0...  
4     [-0.08272361010313034, 0.017822109162807465, 0...  
...                                                 ...  
4432  [-0.062232204, -0.011351791, -0.0027062385, 0....  
4433  [-0.06830623, 0.023115562, 0.028224507, 0.0283...  
4434  [-0.058011707, 0.022569647, 0.0293498, 0.00073...  
4435  [-0.0127937365, 0.002269573, 0.016845196, -0.0...  
4436  [-0.007802535, -0.030409014, -0.01775647, -0.0...  

[44424 rows x 13 columns]

In [54]:
import google.generativeai as genai
import numpy as np
genai.configure(api_key=KEYS.api_key.GOOGLE_API_KEY)

In [77]:
def get_results(top_n = 6,query = "men shirt"):
    query_embedding = genai.embed_content(model="models/text-embedding-004",
                                        content=query,
                                        task_type="retrieval_query")['embedding']
    scores = final_df['embedding'].apply(lambda x: np.dot(x,query_embedding))
    scores = scores.sort_values(ascending=False)[0:top_n]
    return final_df.loc[scores.index][['productDisplayName','link']].to_numpy()

In [78]:
get_results()

array([['French Connection Men Black Shirt',
        'http://assets.myntassets.com/v1/images/style/properties/9a6ead385ff56471fc6f376da807c617_images.jpg'],
       ['Flying Machine Men Check Green Shirts',
        'http://assets.myntassets.com/v1/images/style/properties/3f4c47753110a3f6c093e6bc3e4123df_images.jpg'],
       ['Peter England Men Multi Coloured Casual Shirt',
        'http://assets.myntassets.com/v1/images/style/properties/19d194298ca2009e5cc6f0184f2a0f7d_images.jpg'],
       ['Flying Machine Men Printed White Shirt',
        'http://assets.myntassets.com/v1/images/style/properties/02fc0c611bca206ed4cd2e0bd17bfd8d_images.jpg'],
       ['Flying Machine Men Check Blue Shirts',
        'http://assets.myntassets.com/v1/images/style/properties/c2984f58de4e666b5a3fe6a3b8e36f23_images.jpg'],
       ['Flying Machine Men Check Blue Shirts',
        'http://assets.myntassets.com/v1/images/style/properties/eaca895bbca83fbc080ce26ced471a0d_images.jpg']],
      dtype=object)